In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev5"
args.n_epochs = 12000 
args.init_model = "{}-baseline1".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 3001
args.conn_lambda_epochs_end = 8000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 3001
args.valency_lambda_epochs_end = 8000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 3001
args.euler_lambda_epochs_end = 8000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 8000

args.cross_att_use = False
args.cross_att_random = False
args.cross_att_n_sinkhorn = 1
args.cross_att_use_gcn2 = True
args.cross_att_sigmoid = False
args.ot_lambda = -0.1
# args.morgan_bits = 1024

# args.fgw_no_bonds = False

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=8000, conn_lambda_epochs_start=3001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=1, cross_att_random=False, cross_att_sigmoid=False, cross_att_use=False, cross_att_use_gcn2=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=8000, euler_lambda_epochs_start=3001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', fgw_atoms=True, fgw_bonds=True, init_decoder_model='deepsets-baseline1_decode', init_model='deepsets-baseline1', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=12000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_tra

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

Found previous model mol_opt/output_dev5/deepsets-baseline1/model_deepsets-baseline1_340, epoch 340. Overwriting args.
Penalty params: tau=0.82270 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=340 mode=[0 0 0] conn=True val=True euler=True
Epoch: 341


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:0.2138181
 conn_penalty:0.0000000
 val_penalty:1.5457535
 euler_penalty:1.5154797
 total:0.2168744
Penalty params: tau=0.82222 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=341 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.82222 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=341 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 341, train
 fgw:0.2138181
 conn_penalty:0.0000000
 val_penalty:1.5457535
 euler_penalty:1.5154797
 total:0.2168744
Epoch duration: 5.7012927532196045
Epoch: 342
Losses Batch 0, train
 fgw:0.2050413
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2050413
Penalty params: tau=0.82175 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=342 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.82175 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=342 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 342, train
 fgw:0.2050413
 conn_penalty:0.000

Losses Batch 0, train
 fgw:0.2047279
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2047279
Penalty params: tau=0.81515 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=356 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.81515 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=356 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 356, train
 fgw:0.2047279
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2047279
Epoch duration: 1.0305626392364502
Epoch: 357
Losses Batch 0, train
 fgw:0.2076538
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2076538
Penalty params: tau=0.81468 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=357 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.81468 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=357 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 357, train
 fgw:0.2076538
 conn_penalty:0.000

Losses Batch 0, train
 fgw:0.2203769
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2203769
Penalty params: tau=0.80814 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=371 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.80814 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=371 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 371, train
 fgw:0.2203769
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2203769
Epoch duration: 1.8387517929077148
Epoch: 372
Losses Batch 0, train
 fgw:0.2168866
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:0.2168866
Penalty params: tau=0.80768 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=372 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.80768 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=372 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 372, train
 fgw:0.2168866
 conn_penalty:0.000

...

Losses Batch 0, train
 fgw:168.4506836
 conn_penalty:11.9199585
 val_penalty:42.0400000
 euler_penalty:28.5400000
 total:467.0035156
Penalty params: tau=0.01005 conn_l=2.96180 val_l=4.93230 euler_l=1.97581 epoch=7991 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01005 conn_l=2.96180 val_l=4.93230 euler_l=1.97581 epoch=7991 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7991, train
 fgw:168.4506836
 conn_penalty:11.9199585
 val_penalty:42.0400000
 euler_penalty:28.5400000
 total:467.0035156
Epoch duration: 18.35159134864807
Epoch: 7992
Losses Batch 0, train
 fgw:124.8971387
 conn_penalty:31.1417017
 val_penalty:23.1286206
 euler_penalty:13.6617773
 total:358.2029688
Penalty params: tau=0.01005 conn_l=2.96655 val_l=4.94071 euler_l=1.97882 epoch=7992 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.01005 conn_l=2.96655 val_l=4.94071 euler_l=1.97882 epoch=7992 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7992, train
 fgw:124.8971387
 c

Losses Batch 0, train
 fgw:226.7610937
 conn_penalty:77.3179004
 val_penalty:60.1398340
 euler_penalty:13.3799121
 total:786.1738281
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8006 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8006 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8006, train
 fgw:226.7610937
 conn_penalty:77.3179004
 val_penalty:60.1398340
 euler_penalty:13.3799121
 total:786.1738281
Epoch duration: 12.55841326713562
Epoch: 8007
Losses Batch 0, train
 fgw:235.0284961
 conn_penalty:63.2083496
 val_penalty:85.1599512
 euler_penalty:18.4600000
 total:887.3732812
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8007 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8007 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8007, train
 fgw:235.0284961
 c

Epoch: 8021
Losses Batch 0, train
 fgw:189.9902930
 conn_penalty:24.6767334
 val_penalty:23.2781152
 euler_penalty:15.4381140
 total:411.2872656
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8021 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8021 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8021, train
 fgw:189.9902930
 conn_penalty:24.6767334
 val_penalty:23.2781152
 euler_penalty:15.4381140
 total:411.2872656
Epoch duration: 34.406742811203
Epoch: 8022
Losses Batch 0, train
 fgw:190.1383789
 conn_penalty:28.4913892
 val_penalty:19.2000098
 euler_penalty:12.1800098
 total:395.9725781
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8022 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8022 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8022, train
 fgw:190.

Losses Batch 0, train
 fgw:154.0676270
 conn_penalty:31.0931177
 val_penalty:14.0600000
 euler_penalty:9.4800000
 total:336.6069922
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8036 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8036 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8036, train
 fgw:154.0676270
 conn_penalty:31.0931177
 val_penalty:14.0600000
 euler_penalty:9.4800000
 total:336.6069922
Epoch duration: 17.445846557617188
Epoch: 8037
Losses Batch 0, train
 fgw:155.0370605
 conn_penalty:23.5955054
 val_penalty:20.8200000
 euler_penalty:15.4000000
 total:360.7235938
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8037 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8037 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8037, train
 fgw:155.0370605
 co

KeyboardInterrupt: 